In [1]:
# Работа с табличными данными

import pandas as pd
import numpy as np


# Визуализация

import plotly.express as px
import plotly.io as pio
pio.templates.default = 'plotly_white'
pio.renderers.default = 'notebook'
from motorica.emg8.utils import fig_montage # кастомная функия визуализации


# Пайплайн

# чтение данных и разметка по фактическим жестам
from motorica.emg8.pipeline import read_emg8
# создание экземпляра пайплайна на базе: 
from motorica.emg8.pipeline import create_logreg_pipeline # логистической регрессии
# константы
from motorica.emg8.pipeline import OMG_CH, CMD_COL, GROUP_COL, TARGET


# Метрики
from sklearn.metrics import classification_report


# Для вывода докстрингов с форматированием markdown
from IPython.display import Markdown as md

# Работа с файлами
import os

# Для оценки скорости инференса
from time import time

# Сериализация модели (пайплайна)
import pickle

## Подгрузка и разметка данных

Список имеющихся файлов с данными:

In [2]:
# Папка с файлами данных
DATA_DIR = 'data/new'

montages = sorted(filter(lambda f: f.endswith('.emg8'), os.listdir(DATA_DIR)))
montages

['2024-12-02_14-03-05.emg8',
 '2024-12-04_12-22-13.emg8',
 '2024-12-09_11-22-43.emg8']

In [3]:
montage = montages[-1]
gestures_raw = pd.read_csv(os.path.join(DATA_DIR, montage), sep=' ')
fig_montage(
    gestures_raw[OMG_CH], y_cmd=gestures_raw['id'], 
    title=f"<i>{montage}</i> – исходные данные"
).show()

В качестве отложенной выборки оставим последний цикл протокола:

In [4]:
n_holdout_groups = 1 # отложенная выборка - последний цикл протокола

X_train, X_test, y_train, y_test, gestures, cv_groups = read_emg8(
    montage, 
    n_holdout_groups=n_holdout_groups
)

last_train_idx = gestures[GROUP_COL].drop_duplicates().index[-n_holdout_groups] - 1

print('X_train shape:', X_train.shape)
print('y_train shape:', y_train.shape)
print('X_test shape:', X_test.shape)
print('y_test shape:', y_test.shape)

state_id = gestures[['id', 'state']].drop_duplicates()
GESTURES = state_id['state'] + ' ' + state_id['id'].astype(str)
display(GESTURES)

fig_montage(
    gestures[OMG_CH], y_cmd = gestures[CMD_COL], y_act = gestures[TARGET],
    protocol_cycle = gestures[GROUP_COL],
    title=f"<i>{montage}</i> – разметка по фактическим границам жестов"
).show()

X_train shape: (4355, 16)
y_train shape: (4355,)
X_test shape: (1145, 16)
y_test shape: (1145,)


125          Neutral 0
225     ThumbFingers 1
375            Close 2
525             Open 3
675            Pinch 4
825       Indication 5
975       Wrist_Flex 6
1125    Wrist_Extend 7
dtype: object

## Пайплайн

In [5]:
model = create_logreg_pipeline(optimize_and_fit=True, X=X_train, y=y_train)#, groups=cv_groups)
model

  0%|          | 0/100 [00:00<?, ?it/s]

Pipeline(steps=[('fix_1dim_sample', FixOneDimSample()),
                ('noise_reduct', NoiseReduction()),
                ('add_diff', AddDifference(n_lags=2)),
                ('scaler', MinMaxScaler()),
                ('model',
                 PostprocWrapper(estimator=LogisticRegression(C=1,
                                                              max_iter=5000)))])

In [6]:
# сохранение пайплайна (сериализация)
with open('pipeline_logreg.pkl', 'wb') as f:
    pickle.dump(model, f)

# восстановление пайплайна из файла
with open('pipeline_logreg.pkl', 'rb') as f:
    model = pickle.load(f)

In [7]:
y_train_pred = model.predict(X_train)
y_test_pred = model.predict(X_test)

In [8]:
print("Train data " + '-' * 44)
print(classification_report(y_train, y_train_pred, target_names=GESTURES))

Train data --------------------------------------------
                precision    recall  f1-score   support

     Neutral 0       0.93      0.95      0.94      3086
ThumbFingers 1       0.88      0.85      0.87       187
       Close 2       0.87      0.83      0.85       173
        Open 3       0.89      0.87      0.88       193
       Pinch 4       0.86      0.63      0.72       182
  Indication 5       0.87      0.84      0.85       176
  Wrist_Flex 6       0.87      0.82      0.84       173
Wrist_Extend 7       0.92      0.88      0.90       185

      accuracy                           0.91      4355
     macro avg       0.88      0.83      0.86      4355
  weighted avg       0.91      0.91      0.91      4355



In [9]:
print("Test data " + '-' * 45)
print(classification_report(y_test, y_test_pred, target_names=GESTURES))

Test data ---------------------------------------------
                precision    recall  f1-score   support

     Neutral 0       0.92      0.96      0.94       824
ThumbFingers 1       1.00      0.15      0.26        46
       Close 2       0.91      0.89      0.90        45
        Open 3       0.90      0.88      0.89        50
       Pinch 4       0.87      0.89      0.88        45
  Indication 5       0.91      0.87      0.89        46
  Wrist_Flex 6       0.88      0.86      0.87        42
Wrist_Extend 7       0.81      0.89      0.85        47

      accuracy                           0.91      1145
     macro avg       0.90      0.80      0.81      1145
  weighted avg       0.91      0.91      0.90      1145



## Симуляция инференса в реальном времени на отложенной выборке

In [10]:
y_test_pred = np.empty(0)
comp_durations = np.empty(0)

for i in range(X_test.shape[0]):
    start_time = time()
    #y_test_pred = np.append(y_test_pred, model.predict(X_test[i].reshape(1, -1)))
    y_test_pred = np.append(y_test_pred, model.predict(X_test[i]))
    comp_duration = time() - start_time
    comp_durations = np.append(comp_durations, comp_duration)

print(f"Максимальное время: {np.round(comp_durations.max() * 1000, 2)} мс")
print(f"Среднее время: {np.round(comp_durations.mean() * 1000, 2)} мс")

fig = px.scatter(
    comp_durations * 1000, color=y_test_pred, width=1000, height=500,
    title='Время инференса при последовательных предсказаниях примеров тестовой выборки',
    labels={'value': 'время, мс'}
)
fig.update_coloraxes(showscale=False)
fig.show()

print(classification_report(y_test, y_test_pred, target_names=GESTURES))

fig = fig_montage(
    pd.DataFrame(X_test), 
    y_cmd=gestures.loc[last_train_idx + 1:, CMD_COL].reset_index(drop=True), 
    y_true=y_test, y_pred=y_test_pred,
    title=f"{montage}<br>Результаты последовательных предсказаний примеров тестовой выборки"
)
fig.show()

Максимальное время: 3.1 мс
Среднее время: 0.32 мс


                precision    recall  f1-score   support

     Neutral 0       0.92      0.96      0.94       824
ThumbFingers 1       1.00      0.15      0.26        46
       Close 2       0.91      0.89      0.90        45
        Open 3       0.90      0.88      0.89        50
       Pinch 4       0.87      0.89      0.88        45
  Indication 5       0.91      0.87      0.89        46
  Wrist_Flex 6       0.88      0.86      0.87        42
Wrist_Extend 7       0.89      0.89      0.89        47

      accuracy                           0.91      1145
     macro avg       0.91      0.80      0.82      1145
  weighted avg       0.91      0.91      0.90      1145

